# Training a Linear Regression Model to Predict GPU Performance 

Welcome to our programming project! This is where you'll get to apply the knowledge you obtained in class on a real world project. While the demos are done using SKLearn for simplicity, these programming projects aim to expose you to PyTorch, an industrial library for Machine Learning.


## Introduction

The GPU is a piece of computing hardware first developed in the early 1990s for accelerating graphical applications. Due to its highly parallel nature, people eventually found great uses of GPUs in areas other than gaming. Today, the GPU market is a 20 billion dollar market that serves the fields of video games, AI, crypto, scientific computing and engineering sectors.

In this project, we will train a linear regression model on a GPU dataset -- our goal is to build a web application that takes in the **process node, die area, memory size,** and the number of **millions of transistors** to predict the **compute performance** of that GPU.

## Importing the Necessary Libraries

This project aims to train a linear regression model on the **AMD Radeon and Nvidia GPU Specifications** dataset by  JetBrains Datalore. Here are a list of libraries used in this project:

- **PyTorch**: A powerful machine learning Library
- **PyTorch Lightning**: We only use it for its R2score function
- **Pandas** and **Numpy**: Used for easy data storage and linear algebra
- **SKLearn**: Train test split 
- **Matplotlib** and **Bokeh**: For creating static and dynamic visualizations

In [1]:
import torch
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import PolynomialFeatures
from bokeh.plotting import show, figure, output_notebook


pd.set_option('display.max_colwidth', None)

## Loading the Dataset

The first step is to load and visualize the  dataset. This is crucial in any machine learning development process, as this can give you an idea of what features to include or exclude.

In [2]:
gpu_dataset = pd.read_csv("datasets/gpus_v2.csv")
gpu_dataset = gpu_dataset.sample(frac=1).reset_index(drop=True)
gpu_dataset.head(30)

Manufacturer        Class                      Name  Year  Fab  \
0        Nvidia   Datacenter                   GRID K1  2013   28   
1        Nvidia      Desktop            GeForce GT 640  2013   28   
2    AMD Radeon      Desktop            Radeon HD 8990  2013   28   
3    AMD Radeon      Desktop            Radeon HD 7950  2012   28   
4        Nvidia      Desktop         GeForce 9800 GTX+  2008   55   
5    AMD Radeon      Desktop            Radeon HD 5850  2009   40   
6        Nvidia   Datacenter     Tesla V100 SXM2 16 GB  2019   12   
7        Nvidia      Desktop  GeForce GTX 650 Ti Boost  2013   28   
8    AMD Radeon      Desktop            Radeon HD 4650  2008   55   
9        Nvidia  Workstation           Quadro RTX 5000  2018   12   
10       Nvidia      Desktop            GeForce GT 330  2010   40   
11       Nvidia  Workstation            Quadro FX 5800  2008   55   
12   AMD Radeon      Desktop            Radeon HD 2350  2007   65   
13       Nvidia      Desktop       GeForce GTX 1070 Ti  2017   16   
14       Nvidia   Datacenter               Tesla C2050  2011   40   
15       Nvidia      Desktop               GeForce 210  2009   40   
16       Nvidia      Desktop            GeForce GT 710  2016   28   
17       Nvidia  Workstation            Quadro FX 3700  2008   65   
18       Nvidia  Workstation              Quadro K5000  2012   28   
19       Nvidia   Datacenter                 GRID K520  2013   28   
20       Nvidia  Workstation              Quadro P1000  2017   14   
21       Nvidia      Desktop           GeForce GTS 295  2009   55   
22   AMD Radeon   Datacenter          FirePro S9300 X2  2016   28   
23   AMD Radeon      Desktop             Radeon RX 560  2017   14   
24       Nvidia   Datacenter    Tesla V100S PCIe 32 GB  2019   12   
25   AMD Radeon      Desktop            Radeon HD 7510  2012   40   
26   AMD Radeon      Desktop            Radeon HD 8730  2013   28   
27       Nvidia      Desktop        GeForce GTX 980 Ti  2015   28   
28       Nvidia      Desktop           GeForce 8800 GT  2007   65   
29       Nvidia   Datacenter                GRID K120Q  2014   28   

    Transistors (mln)  Die size  Memory size  Memory speed    GFLOPS    TDP  
0                5080       472        16384        114.04   1305.60  130.0  
1                1020        79         1024         40.10    803.30   49.0  
2                8626       704         6144        576.00   8192.00  375.0  
3                4313       352         3072        240.00    800.00  200.0  
4                 754       260         1024         70.40    470.00  141.0  
5                2154       334         2048        128.00   2088.00  151.0  
6               21100       815        16384        250.00  16350.00  250.0  
7                2540       221         2048        144.20   1505.28  134.0  
8                 514       146         1024         22.40    416.00   48.0  
9               13600       545        16384        448.00  11150.00  230.0  
10                727       144         1024         16.32    240.00   75.0  
11               1400       470         4096        102.40    622.10  189.0  
12                180        85           64          3.20     42.00   20.0  
13               7200       314         8192        320.00   8186.10  300.0  
14               3100       529         3072        144.00   1028.00  238.0  
15                260        57         1024         12.80     44.90   30.5  
16               1020        79         2048         40.00    366.00   19.0  
17                754       324          512         51.20    280.00   78.0  
18               3540       294         4096        172.80   2169.00  122.0  
19               3540       294         8192        320.00   4578.00  225.0  
20               3300       132         4096         80.19   1894.00   47.0  
21               2800       940         1792        223.80   1192.30  289.0  
22              17800      1192         8192       1024.00  15974.00 

Here, we are going to choose the columns `Transistors (mln)`, `Die size`, `Memory size` and `Fab` to be our **training features** and `GFLOPS` to be our **labels**.

In [3]:
features = gpu_dataset[["Transistors (mln)", "Die size", "Memory size", "Fab"]].to_numpy()
labels = gpu_dataset[['GFLOPS']].to_numpy()

print(f"features shape: {features.shape}")
print(f"labels shape: {labels.shape}\n")

X_train, X_test, Y_train, Y_test = train_test_split(features, labels, test_size=0.1)


print(f"X_train shape: {X_train.shape}")
print(f"Y_train shape: {Y_train.shape}")
print(f"X_test shape: {X_test.shape}")
print(f"Y_test shape: {Y_test.shape}")


features shape: (497, 4)
labels shape: (497, 1)

X_train shape: (447, 4)
Y_train shape: (447, 1)
X_test shape: (50, 4)
Y_test shape: (50, 1)


## Prototyping Our First Model (Multi-variate Linear Regression)

Our first model is going to perform Multi-variate linear regression on the data. In PyTorch, we actually have to define our own class (which is a subclass of torch.nn.Module) as well as its `forward()` function.

In [4]:
from torch.nn import Module, MSELoss, Linear
from torch.autograd import Variable
from torch.optim import SGD

class Linreg(Module):
    def __init__(self, inputs, outputs):
        super().__init__()
        """
        Args:
            inputs (int): the input dimensions
            outputs (int): the output dimensions
        """
        
        self.linear = Linear(inputs, outputs)      
        
    def forward(self, x):
        """
        The forward propagation method. This method is used
        by the torch.nn.Module subclass when training or evaluating
        """
        y_pred = self.linear(x)
        return y_pred
    

In [5]:
input_dims, output_dims = (X_train.shape[1], Y_train.shape[1])
learning_rate = 0.000000005
epochs = 50000

In [6]:
model = Linreg(input_dims, output_dims)

optimizer = SGD(model.parameters(), lr=learning_rate)
loss = MSELoss()

In [7]:
inputs = Variable(torch.from_numpy(X_train)).float()
labels = Variable(torch.from_numpy(Y_train)).float()

if __name__ == "__main__":
    for i in range(epochs):

        model.zero_grad()
        pred = model(inputs)
    
        errors = loss(pred, labels)
        print(f"loss of iteration {i+1}: {errors}")
        errors.backward()
        optimizer.step()
    
    

loss of iteration 1: 66877564.0
loss of iteration 2: 43723216.0
loss of iteration 3: 29585782.0
loss of iteration 4: 20939114.0
loss of iteration 5: 15638728.0
loss of iteration 6: 12379881.0
loss of iteration 7: 10368371.0
loss of iteration 8: 9120407.0
loss of iteration 9: 8341039.5
loss of iteration 10: 7850202.0
loss of iteration 11: 7537807.0
loss of iteration 12: 7336392.0
loss of iteration 13: 7204502.0
loss of iteration 14: 7116566.5
loss of iteration 15: 7056738.0
loss of iteration 16: 7015127.5
loss of iteration 17: 6985519.5
loss of iteration 18: 6963968.5
loss of iteration 19: 6947933.5
loss of iteration 20: 6935759.5
loss of iteration 21: 6926346.5
loss of iteration 22: 6918949.0
loss of iteration 23: 6913055.0
loss of iteration 24: 6908298.0
loss of iteration 25: 6904418.0
loss of iteration 26: 6901221.5
loss of iteration 27: 6898562.0
loss of iteration 28: 6896329.5
loss of iteration 29: 6894442.0
loss of iteration 30: 6892826.5
loss of iteration 31: 6891433.5
loss of it

loss of iteration 604: 6705191.5
loss of iteration 605: 6704966.0
loss of iteration 606: 6704741.0
loss of iteration 607: 6704515.0
loss of iteration 608: 6704290.5
loss of iteration 609: 6704066.5
loss of iteration 610: 6703842.0
loss of iteration 611: 6703618.5
loss of iteration 612: 6703395.0
loss of iteration 613: 6703170.5
loss of iteration 614: 6702949.0
loss of iteration 615: 6702724.5
loss of iteration 616: 6702501.0
loss of iteration 617: 6702279.5
loss of iteration 618: 6702057.0
loss of iteration 619: 6701835.5
loss of iteration 620: 6701612.5
loss of iteration 621: 6701391.5
loss of iteration 622: 6701170.5
loss of iteration 623: 6700950.0
loss of iteration 624: 6700729.0
loss of iteration 625: 6700508.5
loss of iteration 626: 6700288.0
loss of iteration 627: 6700067.5
loss of iteration 628: 6699848.0
loss of iteration 629: 6699628.0
loss of iteration 630: 6699409.5
loss of iteration 631: 6699190.5
loss of iteration 632: 6698971.5
loss of iteration 633: 6698753.5
loss of it

loss of iteration 1333: 6592939.0
loss of iteration 1334: 6592839.5
loss of iteration 1335: 6592740.0
loss of iteration 1336: 6592642.0
loss of iteration 1337: 6592541.0
loss of iteration 1338: 6592443.5
loss of iteration 1339: 6592344.0
loss of iteration 1340: 6592244.5
loss of iteration 1341: 6592145.5
loss of iteration 1342: 6592047.0
loss of iteration 1343: 6591947.5
loss of iteration 1344: 6591850.5
loss of iteration 1345: 6591751.5
loss of iteration 1346: 6591654.0
loss of iteration 1347: 6591555.5
loss of iteration 1348: 6591458.0
loss of iteration 1349: 6591359.5
loss of iteration 1350: 6591262.0
loss of iteration 1351: 6591164.0
loss of iteration 1352: 6591066.0
loss of iteration 1353: 6590968.0
loss of iteration 1354: 6590872.0
loss of iteration 1355: 6590775.0
loss of iteration 1356: 6590677.5
loss of iteration 1357: 6590579.5
loss of iteration 1358: 6590483.5
loss of iteration 1359: 6590386.0
loss of iteration 1360: 6590290.0
loss of iteration 1361: 6590192.5
loss of iterat

loss of iteration 2205: 6537106.0
loss of iteration 2206: 6537067.5
loss of iteration 2207: 6537030.0
loss of iteration 2208: 6536991.0
loss of iteration 2209: 6536952.5
loss of iteration 2210: 6536915.5
loss of iteration 2211: 6536877.0
loss of iteration 2212: 6536838.5
loss of iteration 2213: 6536801.0
loss of iteration 2214: 6536763.0
loss of iteration 2215: 6536724.0
loss of iteration 2216: 6536686.0
loss of iteration 2217: 6536648.0
loss of iteration 2218: 6536610.0
loss of iteration 2219: 6536573.0
loss of iteration 2220: 6536534.5
loss of iteration 2221: 6536496.5
loss of iteration 2222: 6536458.5
loss of iteration 2223: 6536421.0
loss of iteration 2224: 6536383.5
loss of iteration 2225: 6536345.5
loss of iteration 2226: 6536308.5
loss of iteration 2227: 6536270.5
loss of iteration 2228: 6536232.5
loss of iteration 2229: 6536195.5
loss of iteration 2230: 6536157.5
loss of iteration 2231: 6536121.5
loss of iteration 2232: 6536083.0
loss of iteration 2233: 6536046.5
loss of iterat

loss of iteration 3082: 6514953.5
loss of iteration 3083: 6514937.5
loss of iteration 3084: 6514923.0
loss of iteration 3085: 6514907.0
loss of iteration 3086: 6514890.5
loss of iteration 3087: 6514875.5
loss of iteration 3088: 6514859.0
loss of iteration 3089: 6514844.0
loss of iteration 3090: 6514827.5
loss of iteration 3091: 6514811.5
loss of iteration 3092: 6514796.0
loss of iteration 3093: 6514781.0
loss of iteration 3094: 6514765.5
loss of iteration 3095: 6514749.5
loss of iteration 3096: 6514734.0
loss of iteration 3097: 6514719.0
loss of iteration 3098: 6514703.5
loss of iteration 3099: 6514687.5
loss of iteration 3100: 6514672.0
loss of iteration 3101: 6514656.0
loss of iteration 3102: 6514641.0
loss of iteration 3103: 6514625.0
loss of iteration 3104: 6514610.0
loss of iteration 3105: 6514594.0
loss of iteration 3106: 6514579.0
loss of iteration 3107: 6514563.0
loss of iteration 3108: 6514547.0
loss of iteration 3109: 6514533.0
loss of iteration 3110: 6514517.5
loss of iterat

...

loss of iteration 46926: 6412507.0
loss of iteration 46927: 6412506.0
loss of iteration 46928: 6412504.5
loss of iteration 46929: 6412503.0
loss of iteration 46930: 6412501.5
loss of iteration 46931: 6412499.0
loss of iteration 46932: 6412498.0
loss of iteration 46933: 6412496.0
loss of iteration 46934: 6412494.5
loss of iteration 46935: 6412494.0
loss of iteration 46936: 6412491.5
loss of iteration 46937: 6412490.5
loss of iteration 46938: 6412488.5
loss of iteration 46939: 6412487.5
loss of iteration 46940: 6412485.5
loss of iteration 46941: 6412483.5
loss of iteration 46942: 6412482.0
loss of iteration 46943: 6412481.0
loss of iteration 46944: 6412479.5
loss of iteration 46945: 6412478.0
loss of iteration 46946: 6412476.5
loss of iteration 46947: 6412474.5
loss of iteration 46948: 6412472.5
loss of iteration 46949: 6412472.5
loss of iteration 46950: 6412469.0
loss of iteration 46951: 6412468.0
loss of iteration 46952: 6412466.0
loss of iteration 46953: 6412464.5
loss of iteration 46

loss of iteration 47751: 6411217.0
loss of iteration 47752: 6411216.0
loss of iteration 47753: 6411214.0
loss of iteration 47754: 6411212.5
loss of iteration 47755: 6411211.5
loss of iteration 47756: 6411209.5
loss of iteration 47757: 6411208.0
loss of iteration 47758: 6411206.5
loss of iteration 47759: 6411205.0
loss of iteration 47760: 6411202.5
loss of iteration 47761: 6411202.0
loss of iteration 47762: 6411200.5
loss of iteration 47763: 6411198.5
loss of iteration 47764: 6411197.0
loss of iteration 47765: 6411196.0
loss of iteration 47766: 6411195.5
loss of iteration 47767: 6411192.5
loss of iteration 47768: 6411190.0
loss of iteration 47769: 6411189.5
loss of iteration 47770: 6411188.0
loss of iteration 47771: 6411185.5
loss of iteration 47772: 6411184.5
loss of iteration 47773: 6411182.0
loss of iteration 47774: 6411181.5
loss of iteration 47775: 6411181.0
loss of iteration 47776: 6411178.0
loss of iteration 47777: 6411177.0
loss of iteration 47778: 6411174.0
loss of iteration 47

loss of iteration 48578: 6409937.0
loss of iteration 48579: 6409936.0
loss of iteration 48580: 6409933.5
loss of iteration 48581: 6409932.5
loss of iteration 48582: 6409930.5
loss of iteration 48583: 6409929.5
loss of iteration 48584: 6409926.5
loss of iteration 48585: 6409925.5
loss of iteration 48586: 6409925.0
loss of iteration 48587: 6409922.0
loss of iteration 48588: 6409921.0
loss of iteration 48589: 6409920.0
loss of iteration 48590: 6409917.5
loss of iteration 48591: 6409917.0
loss of iteration 48592: 6409916.0
loss of iteration 48593: 6409913.5
loss of iteration 48594: 6409912.5
loss of iteration 48595: 6409910.0
loss of iteration 48596: 6409909.0
loss of iteration 48597: 6409907.5
loss of iteration 48598: 6409905.5
loss of iteration 48599: 6409904.5
loss of iteration 48600: 6409902.5
loss of iteration 48601: 6409901.5
loss of iteration 48602: 6409899.0
loss of iteration 48603: 6409898.0
loss of iteration 48604: 6409897.0
loss of iteration 48605: 6409895.0
loss of iteration 48

loss of iteration 49259: 6408892.0
loss of iteration 49260: 6408890.0
loss of iteration 49261: 6408888.5
loss of iteration 49262: 6408887.5
loss of iteration 49263: 6408885.5
loss of iteration 49264: 6408884.5
loss of iteration 49265: 6408882.5
loss of iteration 49266: 6408880.5
loss of iteration 49267: 6408880.0
loss of iteration 49268: 6408877.5
loss of iteration 49269: 6408876.5
loss of iteration 49270: 6408875.0
loss of iteration 49271: 6408873.5
loss of iteration 49272: 6408872.5
loss of iteration 49273: 6408870.0
loss of iteration 49274: 6408869.0
loss of iteration 49275: 6408867.0
loss of iteration 49276: 6408866.0
loss of iteration 49277: 6408864.5
loss of iteration 49278: 6408862.5
loss of iteration 49279: 6408861.0
loss of iteration 49280: 6408859.0
loss of iteration 49281: 6408858.5
loss of iteration 49282: 6408856.5
loss of iteration 49283: 6408854.5
loss of iteration 49284: 6408854.0
loss of iteration 49285: 6408852.5
loss of iteration 49286: 6408850.5
loss of iteration 49

loss of iteration 49943: 6407850.0
loss of iteration 49944: 6407848.5
loss of iteration 49945: 6407848.0
loss of iteration 49946: 6407846.0
loss of iteration 49947: 6407844.0
loss of iteration 49948: 6407842.5
loss of iteration 49949: 6407842.0
loss of iteration 49950: 6407840.5
loss of iteration 49951: 6407839.0
loss of iteration 49952: 6407837.0
loss of iteration 49953: 6407836.0
loss of iteration 49954: 6407833.5
loss of iteration 49955: 6407832.0
loss of iteration 49956: 6407830.5
loss of iteration 49957: 6407829.5
loss of iteration 49958: 6407828.5
loss of iteration 49959: 6407826.5
loss of iteration 49960: 6407824.5
loss of iteration 49961: 6407823.0
loss of iteration 49962: 6407821.5
loss of iteration 49963: 6407819.5
loss of iteration 49964: 6407818.5
loss of iteration 49965: 6407817.5
loss of iteration 49966: 6407816.5
loss of iteration 49967: 6407813.5
loss of iteration 49968: 6407812.5
loss of iteration 49969: 6407811.0
loss of iteration 49970: 6407809.5
loss of iteration 49

In [8]:
from pytorch_lightning.metrics.functional import r2score

test_inputs = Variable(torch.from_numpy(X_test)).float()
test_labels = Variable(torch.from_numpy(Y_test)).float()

model.eval()

with torch.no_grad():
    test_pred = model(test_inputs)
    r2 = r2score(test_pred, test_labels)
    print(r2.item())

0.878578782081604


### Observations

Our first attempt at training a linear regression model provided us with a few observations to note. First is that the loss is huge, even after gradient descent. This is because we are working with huge labels and our output space is very large, so do not be alarmed by the loss. It is better to note the R2 score, which our first model achieved 74%, which is fairly good. Lets fill in the observation table:

| Model | observations | R2 |
| :---- | :----------- | :--- |
| Multi-variate Linear Regerssion | Very large cost, used a very small learning rate | 74% |


## Prototyping Our Second Model (Polynomial Regression)

We are going to train a second model, this time using polynomial regression with cubic features. This in theory should be able to fit a more complicated function to the data.

In [9]:
poly = PolynomialFeatures(degree=3)

X_train_p = poly.fit_transform(X_train)
X_test_p = poly.fit_transform(X_test)
Y_train_p = Y_train
Y_test_p = Y_test

print(f"X_train_p shape: {X_train_p.shape}")
print(f"Y_train_p shape: {Y_train_p.shape}")
print(f"X_test_p shape: {X_test_p.shape}")
print(f"Y_test_p shape: {Y_test_p.shape}")

X_train_p shape: (447, 35)
Y_train_p shape: (447, 1)
X_test_p shape: (50, 35)
Y_test_p shape: (50, 1)


In [10]:
from torch.nn import BatchNorm1d

class Linreg_p(Module):
    def __init__(self, inputs, outputs):
        super().__init__()
        self.linear = Linear(inputs, outputs) 
        self.bn = BatchNorm1d(inputs)
        
    def forward(self, x):
        x = self.bn(x)
        y_pred = self.linear(x)
        return y_pred

In [11]:
input_dims_p, output_dims_p = (X_train_p.shape[1], Y_train_p.shape[1])
learning_rate_p = 0.000001
epochs_p = 50000

In [12]:
model_p = Linreg_p(input_dims_p, output_dims_p)

optimizer_p = SGD(model_p.parameters(), lr=learning_rate_p)
loss_p = MSELoss()

In [13]:
inputs_p = Variable(torch.from_numpy(X_train_p)).float()
labels_p = Variable(torch.from_numpy(Y_train_p)).float()

if __name__ == "__main__":
    for i in range(epochs_p):

        model_p.zero_grad()
        pred_p = model_p(inputs_p)
    
        errors_p = loss(pred_p, labels_p)
        print(f"loss of iteration {i+1}: {errors_p}")
        errors_p.backward()
        optimizer_p.step()
    

loss of iteration 1: 41565788.0
loss of iteration 2: 41564500.0
loss of iteration 3: 41563216.0
loss of iteration 4: 41561932.0
loss of iteration 5: 41560640.0
loss of iteration 6: 41559352.0
loss of iteration 7: 41558068.0
loss of iteration 8: 41556760.0
loss of iteration 9: 41555468.0
loss of iteration 10: 41554164.0
loss of iteration 11: 41552856.0
loss of iteration 12: 41551552.0
loss of iteration 13: 41550228.0
loss of iteration 14: 41548904.0
loss of iteration 15: 41547568.0
loss of iteration 16: 41546232.0
loss of iteration 17: 41544884.0
loss of iteration 18: 41543528.0
loss of iteration 19: 41542168.0
loss of iteration 20: 41540788.0
loss of iteration 21: 41539408.0
loss of iteration 22: 41538016.0
loss of iteration 23: 41536612.0
loss of iteration 24: 41535200.0
loss of iteration 25: 41533768.0
loss of iteration 26: 41532328.0
loss of iteration 27: 41530876.0
loss of iteration 28: 41529404.0
loss of iteration 29: 41527924.0
loss of iteration 30: 41526432.0
loss of iteration 3

loss of iteration 398: 13980532.0
loss of iteration 399: 13859955.0
loss of iteration 400: 13741449.0
loss of iteration 401: 13625008.0
loss of iteration 402: 13510632.0
loss of iteration 403: 13398307.0
loss of iteration 404: 13288028.0
loss of iteration 405: 13179785.0
loss of iteration 406: 13073565.0
loss of iteration 407: 12969357.0
loss of iteration 408: 12867148.0
loss of iteration 409: 12766923.0
loss of iteration 410: 12668665.0
loss of iteration 411: 12572360.0
loss of iteration 412: 12477991.0
loss of iteration 413: 12385538.0
loss of iteration 414: 12294980.0
loss of iteration 415: 12206302.0
loss of iteration 416: 12119481.0
loss of iteration 417: 12034494.0
loss of iteration 418: 11951320.0
loss of iteration 419: 11869938.0
loss of iteration 420: 11790321.0
loss of iteration 421: 11712448.0
loss of iteration 422: 11636297.0
loss of iteration 423: 11561840.0
loss of iteration 424: 11489050.0
loss of iteration 425: 11417907.0
loss of iteration 426: 11348381.0
loss of iterat

loss of iteration 726: 7676601.0
loss of iteration 727: 7672573.0
loss of iteration 728: 7668555.5
loss of iteration 729: 7664544.5
loss of iteration 730: 7660542.5
loss of iteration 731: 7656546.0
loss of iteration 732: 7652560.5
loss of iteration 733: 7648582.0
loss of iteration 734: 7644610.5
loss of iteration 735: 7640647.5
loss of iteration 736: 7636692.5
loss of iteration 737: 7632745.0
loss of iteration 738: 7628806.5
loss of iteration 739: 7624874.5
loss of iteration 740: 7620950.5
loss of iteration 741: 7617035.5
loss of iteration 742: 7613127.5
loss of iteration 743: 7609226.5
loss of iteration 744: 7605334.5
loss of iteration 745: 7601451.0
loss of iteration 746: 7597573.0
loss of iteration 747: 7593704.5
loss of iteration 748: 7589843.5
loss of iteration 749: 7585990.5
loss of iteration 750: 7582144.5
loss of iteration 751: 7578306.5
loss of iteration 752: 7574476.5
loss of iteration 753: 7570653.0
loss of iteration 754: 7566838.5
loss of iteration 755: 7563030.5
loss of it

loss of iteration 1106: 6610925.5
loss of iteration 1107: 6609031.0
loss of iteration 1108: 6607139.5
loss of iteration 1109: 6605250.5
loss of iteration 1110: 6603364.0
loss of iteration 1111: 6601481.5
loss of iteration 1112: 6599602.5
loss of iteration 1113: 6597725.5
loss of iteration 1114: 6595851.5
loss of iteration 1115: 6593980.5
loss of iteration 1116: 6592112.5
loss of iteration 1117: 6590247.0
loss of iteration 1118: 6588384.5
loss of iteration 1119: 6586526.0
loss of iteration 1120: 6584669.0
loss of iteration 1121: 6582815.0
loss of iteration 1122: 6580964.0
loss of iteration 1123: 6579116.5
loss of iteration 1124: 6577270.0
loss of iteration 1125: 6575428.0
loss of iteration 1126: 6573588.5
loss of iteration 1127: 6571751.5
loss of iteration 1128: 6569917.0
loss of iteration 1129: 6568085.0
loss of iteration 1130: 6566257.5
loss of iteration 1131: 6564430.5
loss of iteration 1132: 6562607.0
loss of iteration 1133: 6560786.5
loss of iteration 1134: 6558968.0
loss of iterat

loss of iteration 1444: 6067666.0
loss of iteration 1445: 6066161.0
loss of iteration 1446: 6064655.5
loss of iteration 1447: 6063150.0
loss of iteration 1448: 6061644.0
loss of iteration 1449: 6060137.5
loss of iteration 1450: 6058631.0
loss of iteration 1451: 6057124.5
loss of iteration 1452: 6055617.5
loss of iteration 1453: 6054109.0
loss of iteration 1454: 6052600.5
loss of iteration 1455: 6051092.5
loss of iteration 1456: 6049583.5
loss of iteration 1457: 6048075.0
loss of iteration 1458: 6046565.5
loss of iteration 1459: 6045055.5
loss of iteration 1460: 6043545.5
loss of iteration 1461: 6042034.5
loss of iteration 1462: 6040524.5
loss of iteration 1463: 6039012.5
loss of iteration 1464: 6037501.0
loss of iteration 1465: 6035990.0
loss of iteration 1466: 6034476.5
loss of iteration 1467: 6032962.5
loss of iteration 1468: 6031450.0
loss of iteration 1469: 6029935.5
loss of iteration 1470: 6028421.5
loss of iteration 1471: 6026907.0
loss of iteration 1472: 6025392.0
loss of iterat

...

loss of iteration 48606: 2023964.125
loss of iteration 48607: 2023951.875
loss of iteration 48608: 2023940.25
loss of iteration 48609: 2023929.25
loss of iteration 48610: 2023917.25
loss of iteration 48611: 2023905.375
loss of iteration 48612: 2023893.625
loss of iteration 48613: 2023881.875
loss of iteration 48614: 2023870.25
loss of iteration 48615: 2023858.125
loss of iteration 48616: 2023846.375
loss of iteration 48617: 2023834.5
loss of iteration 48618: 2023822.625
loss of iteration 48619: 2023811.25
loss of iteration 48620: 2023799.75
loss of iteration 48621: 2023787.375
loss of iteration 48622: 2023775.625
loss of iteration 48623: 2023764.0
loss of iteration 48624: 2023753.125
loss of iteration 48625: 2023740.75
loss of iteration 48626: 2023729.0
loss of iteration 48627: 2023717.625
loss of iteration 48628: 2023705.375
loss of iteration 48629: 2023693.75
loss of iteration 48630: 2023682.25
loss of iteration 48631: 2023670.75
loss of iteration 48632: 2023658.75
loss of iteration 

loss of iteration 48922: 2020279.25
loss of iteration 48923: 2020267.75
loss of iteration 48924: 2020256.375
loss of iteration 48925: 2020245.5
loss of iteration 48926: 2020233.5
loss of iteration 48927: 2020221.875
loss of iteration 48928: 2020210.375
loss of iteration 48929: 2020199.0
loss of iteration 48930: 2020186.875
loss of iteration 48931: 2020175.625
loss of iteration 48932: 2020163.875
loss of iteration 48933: 2020152.375
loss of iteration 48934: 2020141.375
loss of iteration 48935: 2020129.625
loss of iteration 48936: 2020117.75
loss of iteration 48937: 2020106.75
loss of iteration 48938: 2020095.0
loss of iteration 48939: 2020083.875
loss of iteration 48940: 2020071.625
loss of iteration 48941: 2020060.25
loss of iteration 48942: 2020048.75
loss of iteration 48943: 2020036.75
loss of iteration 48944: 2020025.25
loss of iteration 48945: 2020013.5
loss of iteration 48946: 2020002.625
loss of iteration 48947: 2019991.5
loss of iteration 48948: 2019979.5
loss of iteration 48949

loss of iteration 49255: 2016465.0
loss of iteration 49256: 2016453.875
loss of iteration 49257: 2016443.0
loss of iteration 49258: 2016431.125
loss of iteration 49259: 2016419.875
loss of iteration 49260: 2016408.625
loss of iteration 49261: 2016396.875
loss of iteration 49262: 2016385.875
loss of iteration 49263: 2016374.25
loss of iteration 49264: 2016363.125
loss of iteration 49265: 2016351.375
loss of iteration 49266: 2016340.25
loss of iteration 49267: 2016329.25
loss of iteration 49268: 2016318.0
loss of iteration 49269: 2016306.5
loss of iteration 49270: 2016295.375
loss of iteration 49271: 2016283.625
loss of iteration 49272: 2016272.75
loss of iteration 49273: 2016261.125
loss of iteration 49274: 2016249.5
loss of iteration 49275: 2016238.375
loss of iteration 49276: 2016226.875
loss of iteration 49277: 2016216.0
loss of iteration 49278: 2016204.875
loss of iteration 49279: 2016192.75
loss of iteration 49280: 2016181.75
loss of iteration 49281: 2016170.375
loss of iteration 4

loss of iteration 49528: 2013390.875
loss of iteration 49529: 2013379.0
loss of iteration 49530: 2013368.0
loss of iteration 49531: 2013356.625
loss of iteration 49532: 2013345.75
loss of iteration 49533: 2013334.375
loss of iteration 49534: 2013323.125
loss of iteration 49535: 2013312.125
loss of iteration 49536: 2013301.125
loss of iteration 49537: 2013290.125
loss of iteration 49538: 2013278.75
loss of iteration 49539: 2013267.625
loss of iteration 49540: 2013256.625
loss of iteration 49541: 2013245.625
loss of iteration 49542: 2013234.0
loss of iteration 49543: 2013223.0
loss of iteration 49544: 2013211.875
loss of iteration 49545: 2013200.375
loss of iteration 49546: 2013188.875
loss of iteration 49547: 2013177.875
loss of iteration 49548: 2013167.125
loss of iteration 49549: 2013156.125
loss of iteration 49550: 2013144.375
loss of iteration 49551: 2013133.75
loss of iteration 49552: 2013122.375
loss of iteration 49553: 2013111.25
loss of iteration 49554: 2013100.0
loss of iterati

loss of iteration 49842: 2009910.875
loss of iteration 49843: 2009899.25
loss of iteration 49844: 2009888.875
loss of iteration 49845: 2009877.375
loss of iteration 49846: 2009866.625
loss of iteration 49847: 2009855.625
loss of iteration 49848: 2009844.75
loss of iteration 49849: 2009833.625
loss of iteration 49850: 2009821.875
loss of iteration 49851: 2009811.75
loss of iteration 49852: 2009800.5
loss of iteration 49853: 2009789.625
loss of iteration 49854: 2009778.875
loss of iteration 49855: 2009767.625
loss of iteration 49856: 2009756.625
loss of iteration 49857: 2009745.375
loss of iteration 49858: 2009734.625
loss of iteration 49859: 2009723.75
loss of iteration 49860: 2009712.5
loss of iteration 49861: 2009702.25
loss of iteration 49862: 2009690.75
loss of iteration 49863: 2009679.75
loss of iteration 49864: 2009668.875
loss of iteration 49865: 2009658.0
loss of iteration 49866: 2009646.875
loss of iteration 49867: 2009635.75
loss of iteration 49868: 2009624.875
loss of iterati

In [14]:
test_inputs_p = Variable(torch.from_numpy(X_test_p)).float()
test_labels_p = Variable(torch.from_numpy(Y_test_p)).float()

model_p.eval()

with torch.no_grad():
    test_pred_p = model_p(test_inputs_p)
    r2_p = r2score(test_pred_p, test_labels_p)
    print(r2_p.item())

0.9484679698944092


This looks even better! I think this model is ready for use. Before we save the model, lets record the observations in the table below:

| Model | observations | R2 |
| :---- | :----------- | :--- |
| Multi-variate Linear Regerssion | Very large cost, used a very small learning rate | 74% |
| Polynomial Regression | Cost is smaller but still large. This is no issue | 93% |

In [15]:
if __name__ == "__main__":
    torch.save(model_p.state_dict(), "gpu-predictor.pt")

## References

1. https://www.alliedmarketresearch.com/graphic-processing-unit-market
2. https://pytorch.org/docs/stable/generated/torch.nn.Module.html#torch.nn.Module